# Prepare excel read with pandas

In [1]:
import pandas as pd
# data = pd.read_excel(r'monthly_market_data - Copy.xlsx')
data = pd.read_excel(r'monthly_market_data - Copy (2).xlsx')

# print(data)


# Read Excel to memnory and create classes

In [2]:

class CompanyInfo:
    def __init__(self, tickerKey, name, month, marketcap, close):
        self.tickerKey = tickerKey
        self.name = name
        self.month = month
        self.rollingAverage = None
        self.marketcap = marketcap
        self.close = close
        self.closeAdjust = close
        self.momentum = None
        self.size = None

    def __repr__(self):
         return "tickerKey:"+str(self.tickerKey) + "\t month:" + str(self.month) + "\t close:" + str(self.close)+ "\t rollingAverage:" + str(self.rollingAverage)+ "\t momentum:" + str(self.momentum)+ "\t size:" + str(self.size)+"\n"

    def __str__(self):
                  return "tickerKey:"+str(self.tickerKey) + "\t month:" + str(self.month) + "\t close:" + str(self.close)+ "\t rollingAverage:" + str(self.rollingAverage)+ "\t momentum:" + str(self.momentum)+ "\t size:" + str(self.size)+"\n"


companyInfoList = []

for i, companyInfoPandas in data.iterrows():
    companyInfoList.append(CompanyInfo(tickerKey=companyInfoPandas["TickerKey"],
                                       name=companyInfoPandas["TickerNamePooyaFA"],
                                       month=companyInfoPandas["DayKeyFA"]// 100,
                                       marketcap=companyInfoPandas["marketcap"],
                                       close=companyInfoPandas["Close"],
                                       ))
print(companyInfoList[:5])

[tickerKey:1	 month:139712	 close:1653	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139801	 close:2935	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139802	 close:3194	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139803	 close:3477	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139804	 close:3730	 rollingAverage:None	 momentum:None	 size:None
]


# Extract company names

In [3]:
companyTickerSet = list(set([companyInfo.tickerKey for companyInfo in companyInfoList]))
print(companyTickerSet[0])


1


# Extract company months

In [4]:
allMonths = list(set([companyInfo.month for companyInfo in companyInfoList]))
allMonths.sort()
print(allMonths)
print("Total:",len(allMonths))

[138001, 138002, 138003, 138004, 138005, 138006, 138007, 138008, 138009, 138010, 138011, 138012, 138101, 138102, 138103, 138104, 138105, 138106, 138107, 138108, 138109, 138110, 138111, 138112, 138201, 138202, 138203, 138204, 138205, 138206, 138207, 138208, 138209, 138210, 138211, 138212, 138301, 138302, 138303, 138304, 138305, 138306, 138307, 138308, 138309, 138310, 138311, 138312, 138401, 138402, 138403, 138404, 138405, 138406, 138407, 138408, 138409, 138410, 138411, 138412, 138501, 138502, 138503, 138504, 138505, 138506, 138507, 138508, 138509, 138510, 138511, 138512, 138601, 138602, 138603, 138604, 138605, 138606, 138607, 138608, 138609, 138610, 138611, 138612, 138701, 138702, 138703, 138704, 138705, 138706, 138707, 138708, 138709, 138710, 138711, 138712, 138801, 138802, 138803, 138804, 138805, 138806, 138807, 138808, 138809, 138810, 138811, 138812, 138901, 138902, 138903, 138904, 138905, 138906, 138907, 138908, 138909, 138910, 138911, 138912, 139001, 139002, 139003, 139004, 139005,

# Fill missing close adjust

In [5]:
def calculateCloseAdjust(companyHistoricalData, allMonths, monthIndex):
  privuseMonthCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[monthIndex - 1]]
  if len(privuseMonthCompanyInfo) == 0:
    return None
  privuseMonthCompanyInfo:CompanyInfo = privuseMonthCompanyInfo[0]
  nextMonthCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[monthIndex + 1 ]]

  if len(nextMonthCompanyInfo) == 1:
    nextMonthCompanyInfo:CompanyInfo = nextMonthCompanyInfo[0]
    return privuseMonthCompanyInfo.closeAdjust * (1 + (nextMonthCompanyInfo.closeAdjust - privuseMonthCompanyInfo.closeAdjust )   / privuseMonthCompanyInfo.closeAdjust) ** (1/2)

  if monthIndex + 2 == len(allMonths):
    return None
  secondNextMonthCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[monthIndex + 2 ]]
  if len(secondNextMonthCompanyInfo) == 0:
    return None
  secondNextMonthCompanyInfo:CompanyInfo = secondNextMonthCompanyInfo[0]
  return privuseMonthCompanyInfo.closeAdjust * (1 + (secondNextMonthCompanyInfo.closeAdjust - privuseMonthCompanyInfo.closeAdjust )   / privuseMonthCompanyInfo.closeAdjust) ** (1/3)
  # print(calculatedCloseAdjust)


for tickerKey in companyTickerSet:
  companyHistoricalData = [companyInfo for companyInfo in companyInfoList if companyInfo.tickerKey == tickerKey]
  for month in range(1,len(allMonths)-1):
    currentCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[month]]
    if len(currentCompanyInfo) > 1:
        raise Exception("A company cannot have two similar months:"+ tickerKey+" month:"+ allMonths[month])
    if len(currentCompanyInfo) == 1:
        continue
    if len(currentCompanyInfo) == 0:
      closeAdjust = calculateCloseAdjust(companyHistoricalData,allMonths,month)
      if closeAdjust is None: continue
      # print(closeAdjust)
      if type(closeAdjust) != float :
        print("different type " ,(closeAdjust))

      adjustedCompanyInfo = CompanyInfo(tickerKey,companyHistoricalData[0].name,allMonths[month],None,None)
      adjustedCompanyInfo.closeAdjust = closeAdjust
      companyInfoList.append(adjustedCompanyInfo)
      # print(tickerKey,allMonths[month]) # log adjusted


# Test data

In [6]:
dataToShow = [[companyInfo.closeAdjust,companyInfo.month] for companyInfo in companyInfoList if companyInfo.tickerKey == 9]
dataToShow = dataToShow.sort(key=operator.attrgetter("month"), reverse=False)
print(dataToShow)

[5120, 5350, 5499, 5742, 6135, 6008, 5906, 6280, 6294, 6034, 5603, 5350, 5519, 5200, 5375, 5750, 4561, 4679, 4522, 4705, 5500, 5302, 5039, 3622, 3504, 3103, 3237, 2504, 2609, 2468, 2543, 3185, 2969, 2934, 2850, 2655, 2581, 3829, 3450, 3072, 3647, 4047, 4226, 5055, 5233, 4772, 4552, 4425, 1983, 1871, 1710, 2134, 1976, 1732, 1742, 1961, 2012, 2212, 2617, 2961, 2947, 2925, 2084, 2060, 2068, 2006, 2046, 1848, 1850, 1901, 1874, 1913, 1922, 1891, 1893, 1913, 1773, 1779, 1785, 1790, 1978, 2025, 2102, 2118, 2123, 2791, 2662, 2657, 2290, 1936, 2070, 2161, 2332, 2488, 2593, 2836, 3083, 3662, 3168, 2865, 3000, 2800, 2664, 2750, 2870, 3050, 3130, 3425, 3182, 3600, 3699, 3850, 4079, 3363, 3600, 3332, 3301, 3240, 3216, 3610, 3521, 3320, 3749, 3339, 3135, 2700, 2640, 2590, 2517, 2600, 2415, 2660, 3805, 3411, 3500, 3400, 3509, 3800, 5094, 22036, 22350, 24181, 25379, 25304, 26859, 24832, 25780, 6100, 5440, 5219, 4480, 5132, 5000, 4839, 4950, 5000, 4912, 4490, 3767, 3102, 3060, 2782, 2685, 2554, 2360, 2

# Calculate rolling average

In [7]:
def getRollingDataWindow(companyHistoricalData,allMonths,rollingWindowSize,endMonthIndex):
  rollingDataWindow = []
  for monthIndex in range(endMonthIndex+1 - rollingWindowSize,endMonthIndex+1):
    currentCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[monthIndex]]
    if len(currentCompanyInfo) == 0:
        return rollingDataWindow
    if len(currentCompanyInfo) > 1:
        raise Exception("A company cannot have two similar months:"+ tickerKey+" month:"+ allMonths[monthIndex])
    rollingDataWindow.append(currentCompanyInfo[0])
  return rollingDataWindow

In [8]:
def average(dataList):
    if len(dataList)==0:
        return None
    data = [info.closeAdjust for info in dataList]
    # print(data)
    return sum(data) / len(dataList)

# print(companyInfoList)
rollingAverageWindowSize = 12
for tickerKey in companyTickerSet:
    # print("tickerKey",tickerKey)
    companyHistoricalData = [companyInfo for companyInfo in companyInfoList if companyInfo.tickerKey == tickerKey]
    for endMonthIndex in range(rollingAverageWindowSize-1,len(allMonths)):
      # print("endMonthIndex",endMonthIndex)
      rollingDataWindow = getRollingDataWindow(companyHistoricalData,allMonths, rollingAverageWindowSize,endMonthIndex)
      if len(rollingDataWindow) != rollingAverageWindowSize: continue
      currentCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[endMonthIndex]]
      currentCompanyInfo:CompanyInfo = currentCompanyInfo[0]
      currentCompanyInfo.rollingAverage = average(rollingDataWindow)

# print(companyInfoList)

tickerKey 1
endMonthIndex 11
endMonthIndex 12
endMonthIndex 13
endMonthIndex 14
endMonthIndex 15
endMonthIndex 16
endMonthIndex 17
endMonthIndex 18
endMonthIndex 19
endMonthIndex 20
endMonthIndex 21
endMonthIndex 22
endMonthIndex 23
endMonthIndex 24
endMonthIndex 25
endMonthIndex 26
endMonthIndex 27
endMonthIndex 28
endMonthIndex 29
endMonthIndex 30
endMonthIndex 31
endMonthIndex 32
endMonthIndex 33
endMonthIndex 34
endMonthIndex 35
endMonthIndex 36
endMonthIndex 37
endMonthIndex 38
endMonthIndex 39
endMonthIndex 40
endMonthIndex 41
endMonthIndex 42
endMonthIndex 43
endMonthIndex 44
endMonthIndex 45
endMonthIndex 46
endMonthIndex 47
endMonthIndex 48
endMonthIndex 49
endMonthIndex 50
endMonthIndex 51
endMonthIndex 52
endMonthIndex 53
endMonthIndex 54
endMonthIndex 55
endMonthIndex 56
endMonthIndex 57
endMonthIndex 58
endMonthIndex 59
endMonthIndex 60
endMonthIndex 61
endMonthIndex 62
endMonthIndex 63
endMonthIndex 64
endMonthIndex 65
endMonthIndex 66
endMonthIndex 67
endMonthIndex 68
en

In [ ]:
# Old code that is complicated

# import operator
# rollingAverageWindowSize = 12
# for tickerKey in companyTickerSet:
#     companyHistoricalData = [companyInfo for companyInfo in companyInfoList if companyInfo.tickerKey == tickerKey]
#     print(companyHistoricalData[:10])
#     for monthRange in range(rollingAverageWindowSize-1,len(allMonths)):
#         currentCompanyInfo = [x for x in companyHistoricalData if x.month == allMonths[monthRange]]
#         closedMonths = 0
#         rollingAverage = 0
#         if len(currentCompanyInfo)==0:
#             continue
#         currentCompanyInfo = currentCompanyInfo[0]
#         for month in range(monthRange+1-rollingAverageWindowSize,monthRange+1):
#             companyInfo = [x for x in companyHistoricalData if x.month == allMonths[month]]
#             if len(companyInfo)==0:
#                 closedMonths+=1
#                 continue
#             companyInfo = companyInfo[0]
#             rollingAverage += companyInfo.close / rollingAverageWindowSize
#         if closedMonths > 2:
#             currentCompanyInfo.rollingAverage = None
#         else:
#             currentCompanyInfo.rollingAverage = rollingAverage
#             currentCompanyInfo.rollingAverageClosedMonths = closedMonths


[tickerKey:1	 month:139712	 close:1653	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139801	 close:2935	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139802	 close:3194	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139803	 close:3477	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139804	 close:3730	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139805	 close:5143	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139806	 close:6305	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139807	 close:4974	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139808	 close:5965	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:1	 month:139809	 close:7536	 rollingAverage:None	 momentum:None	 size:None
]
[tickerKey:9	 month:138001	 close:5120	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:9	 month:138002	 close:5350	 ro

In [ ]:
print(companyHistoricalData)

[tickerKey:106470	 month:140002	 close:7883	 rollingAverage:None	 momentum:None	 size:None
, tickerKey:106470	 month:140003	 close:15370	 rollingAverage:None	 momentum:None	 size:None
]


In [ ]:
[x for x in companyHistoricalData if x.rollingAverage is not None][:10]

[]

# set size

In [ ]:
for month in allMonths:
    companiesInMonth = [x for x in companyInfoList if x.month== month]
    companiesInMonth.sort(key=operator.attrgetter("marketcap"), reverse=True)
    for company in companiesInMonth[0:len(companiesInMonth) // 2]:
        company.size = "Big"
    for company in companiesInMonth[len(companiesInMonth) // 2:]:
        company.size = "Small"

print ([x for x in companiesInMonth if x.size ][-10:])

[tickerKey:1215	 month:140004	 close:4600	 rollingAverage:7026.666666666667	 momentum:None	 size:Small
, tickerKey:239	 month:140004	 close:78810	 rollingAverage:132200.8333333333	 momentum:None	 size:Small
, tickerKey:3006	 month:140004	 close:24390	 rollingAverage:38716.74999999999	 momentum:None	 size:Small
, tickerKey:1413	 month:140004	 close:15440	 rollingAverage:17971.666666666664	 momentum:None	 size:Small
, tickerKey:74108	 month:140004	 close:16901	 rollingAverage:13821.916666666668	 momentum:None	 size:Small
, tickerKey:2769	 month:140004	 close:9794	 rollingAverage:27161.416666666664	 momentum:None	 size:Small
, tickerKey:2551	 month:140004	 close:6868	 rollingAverage:33387.0	 momentum:None	 size:Small
, tickerKey:76298	 month:140004	 close:19300	 rollingAverage:23567.499999999996	 momentum:None	 size:Small
, tickerKey:2511	 month:140004	 close:5314	 rollingAverage:4999.75	 momentum:None	 size:Small
, tickerKey:74132	 month:140004	 close:19517	 rollingAverage:None	 momentum

In [ ]:
for month in allMonths:
    companiesInMonth = [x for x in companyInfoList if x.month== month and x.rollingAverage is not None]
    companiesInMonth.sort(key=operator.attrgetter("rollingAverage"), reverse=True)
    for company in companiesInMonth[0:len(companiesInMonth) // 2]:
        company.momentum = "High"
    for company in companiesInMonth[len(companiesInMonth) // 2:]:
        company.momentum = "Low"

print ([x for x in companyInfoList if x.rollingAverage ][-20:])

[tickerKey:108032	 month:139809	 close:10690	 rollingAverage:6978.583333333332	 momentum:Low	 size:Big
, tickerKey:108032	 month:139810	 close:13728	 rollingAverage:7687.583333333332	 momentum:Low	 size:Big
, tickerKey:108032	 month:139811	 close:20306	 rollingAverage:8954.916666666666	 momentum:High	 size:Big
, tickerKey:108032	 month:139812	 close:27570	 rollingAverage:10734.083333333332	 momentum:High	 size:Big
, tickerKey:108032	 month:139901	 close:40903	 rollingAverage:13565.0	 momentum:High	 size:Big
, tickerKey:108032	 month:139902	 close:35193	 rollingAverage:15964.416666666668	 momentum:High	 size:Big
, tickerKey:108032	 month:139903	 close:48245	 rollingAverage:19476.416666666668	 momentum:High	 size:Big
, tickerKey:108032	 month:139904	 close:60837	 rollingAverage:24017.0	 momentum:High	 size:Big
, tickerKey:108032	 month:139905	 close:45514	 rollingAverage:27127.416666666668	 momentum:High	 size:Big
, tickerKey:108032	 month:139906	 close:48010	 rollingAverage:30423.5	 mom

# rolling average factor

In [ ]:


def findCompanyInfo(companyInfoListToSearch, month, tickerKey):
    for companyInfo in companyInfoListToSearch:
        if companyInfo.month == month and companyInfo.tickerKey == tickerKey:
            return companyInfo
    return None


MoM = {}

for index,month in enumerate(allMonths[:-1]):
    # Get companies of corrent month
    companiesInMonth = [x for x in companyInfoList if x.month== month]
    companiesInNextMonth = [x for x in companyInfoList if x.month== allMonths[index+1]]
    # Get companis for these filters SL SH BL BH
    SL = [company for company in companiesInMonth if company.size == "Small" and company.momentum == "Low"]
    SH = [company for company in companiesInMonth if company.size == "Small" and company.momentum == "High"]
    BL = [company for company in companiesInMonth if company.size == "Big" and company.momentum == "Low"]
    BH = [company for company in companiesInMonth if company.size == "Big" and company.momentum == "High"]
    # Get companies next month info
    BH_average = [findCompanyInfo(companiesInNextMonth,allMonths[index+1],company.tickerKey) for company in BH]
    BL_average = [findCompanyInfo(companiesInNextMonth,allMonths[index+1],company.tickerKey) for company in BL]
    SH_average = [findCompanyInfo(companiesInNextMonth,allMonths[index+1],company.tickerKey) for company in SH]
    SL_average = [findCompanyInfo(companiesInNextMonth,allMonths[index+1],company.tickerKey) for company in SL]
    # Get companies next month close
    BH_average = average([x.close for x in BH_average if x is not None])
    BL_average = average([x.close for x in BL_average if x is not None])
    SH_average = average([x.close for x in SH_average if x is not None])
    SL_average = average([x.close for x in SL_average if x is not None])
    
    # If all were filled, Add to MOM
    if (BH_average and BL_average and SH_average and SL_average ):
        MoM[month]=(0.5 * (SH_average + BH_average) - 0.5 * (SL_average + BL_average))

print(MoM)


{138012: 11415.486102495175, 138101: 12705.69088362069, 138102: 12097.854497354498, 138103: 14204.090162907269, 138104: 12501.00187969925, 138105: 12008.96962095875, 138106: 11450.746274741341, 138107: 12966.256628900815, 138108: 14587.543810786916, 138109: 15280.179801745318, 138110: 14676.545281385283, 138111: 13571.126875984426, 138112: 15225.607438689563, 138201: 14109.147826688813, 138202: 14717.744763378343, 138203: 14842.072712722262, 138204: 17190.92382964916, 138205: 13902.200253048079, 138206: 12032.240238694423, 138207: 12487.769047619047, 138208: 14313.114670823401, 138209: 14194.104376526255, 138210: 14976.340666478132, 138211: 13993.243421052633, 138212: 14070.757190635453, 138301: 12933.915503339565, 138302: 11218.19810298103, 138303: 10344.496915584416, 138304: 13896.43102361634, 138305: 8885.21067927171, 138306: 9046.89773063697, 138307: 11008.110050505049, 138308: 9551.552467105263, 138309: 9045.454040404042, 138310: 10622.73393424473, 138311: 7860.6630312949455, 1383